<h1>Limpieza y análisis exploratorio de la base de datos Registro Mercantil de la Cámara de Comercio de Cali </h1>

In [1]:
#Cargamos los paquetes que vamos a necesitar
import pandas as pd
import numpy as np
from pandas_profiling import ProfileReport

# Visualisation
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go


In [2]:
# Se lee la base de datos
# IMPORTANTE: se debe cambiar el nombre de la base de datos al igual que la dirección URL. Preferiblemente que los datos estén en la misma carpeta que el notebook (.ipynb)
# Esta línea es para leerlos en formato EXCEL
df = pd.read_excel('RM_2019_V1.xlsx', dtype={'CODIGO_CIIU':object, 'MATRICULA': object, 'NIT':object, 'Año de FECHA_RENOVACION':object, 'PATRIMONIO': np.int, 'UTILIDAD_PERDIDA': np.int, 'VENTA': np.int, 'UTILIDAD_BRUTA': np.int, 'ESTABLECIMIENTOS': np.int})
# Esta línea es para leerlos en formato CSV especificando la clase de los objetos que necesitamos en la base
# df = pd.read_csv('C:/Users/ortiz/Downloads/BD_Marketing.csv', encoding='latin-1', dtype={'CODIGO_CIIU':object, 'MATRICULA': object, 'CIIU_COR': object, 'DIVISION': object, 'GRUPO': object})
pd.set_option('display.max_columns', None)
print(df.info())
df.head(2)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 123590 entries, 0 to 123589
Data columns (total 34 columns):
 #   Column                   Non-Null Count   Dtype         
---  ------                   --------------   -----         
 0   MATRICULA                123590 non-null  object        
 1   NIT                      123590 non-null  object        
 2   CONSECUTIVO_PROPIETARIO  123548 non-null  float64       
 3   MAT_REN                  123590 non-null  object        
 4   ESTADO_MAT_REN           123590 non-null  object        
 5   ESTADO_ACTUAL            123590 non-null  object        
 6   RAZON_SOCIAL             123585 non-null  object        
 7   SECTOR                   123590 non-null  object        
 8   CODIGO_CIIU              123590 non-null  object        
 9   DESC_CIIU                123590 non-null  object        
 10  NOM_ENTE_JURIDICO        123590 non-null  object        
 11  PN_PJ                    123590 non-null  object        
 12  DESC_TAMANO     

MATRICULA        NIT  CONSECUTIVO_PROPIETARIO     MAT_REN ESTADO_MAT_REN  \
0        60  890306499                      0.0  Renovacion              D   
1        64  860026759                      0.0  Renovacion              D   

  ESTADO_ACTUAL                                       RAZON_SOCIAL SECTOR  \
0        ACTIVO  UNION PLASTICA S.A.S.                         ...      C   
1        ACTIVO  CARTONES AMERICA S.A. CAME                    ...      C   

  CODIGO_CIIU                                          DESC_CIIU  \
0        2229  FABRICACIÓN DE ARTÍCULOS DE PLÁSTICO N.C.P.   ...   
1        1702  FABRICACIÓN DE PAPEL Y CARTÓN ONDULADO (CORRUG...   

                                   NOM_ENTE_JURIDICO             PN_PJ  \
0  Sociedad por Acciones Simplificada            ...  Persona jurídica   
1  Sociedad Anónima                              ...  Persona jurídica   

  DESC_TAMANO TAMANO957 CIUDAD Año de FECHA_RENOVACION FECHA_MATRICULA  \
0      GRANDE   MEDIANA  Yumbo                    2020      1972-01-12   
1      GRANDE    GRANDE   Cali                    2020      1972-01-12   

              FECHA_MAT_REN                              EMAIL   TELEFONO  \
0  12/03/2019 10:43:58 a.m.          uniplas@unionplastica.com  6644425.0   
1   28/03/2019 2:34:03 p.m.  evelyn.bustos@cartonesamerica.com  6818888.0   

                 BARRIO        COMUNA  \
0          Barrio Yumbo  Comuna Yumbo   
1  Brisas De Los Alamos     Comuna 02   

                                 DIRECCION_COMERCIAL  \
0  KR 39 # 12 A - 151 ACOPI                      ...   
1  CL 70 NORTE # 2 A - 130                       ...   

                        REP_LEGAL AFILIADO  PORCENT_EXTRANJERO  PATRIMONIO  \
0  JOSÉ GUILLERMO PARDO BORRERO          S                 0.0 -2147483648   
1  PIERANGELO  PACINI BLANCO             S                30.0 -2147483648   

   PERSONAL_OCUPADO   TOT_ACTIVOS  UTILILIDAD_PERDIDA        VENTAS  \
0             154.0   28967302509        9.723515e+08  1.794953e+10   
1             405.0  454622201000        5.599716e+10  3.158669e+11   

     TOT_PASIVO  UTILILIDAD_BRUTA  ESTABLECIMIENTOS  
0    4277348867      8.727068e+08                 1  
1  277842326000      3.379944e+10                 2

In [3]:
# Se cambian los nombres de las variables para facilitar su interpretación
df.rename(columns={'Año de FECHA_RENOVACION':'ULTIMO_ANO_RENOVADO',
                          'FECHA_MAT_REN':'FECHA_MATRICULA_RENOVACION_HORA',
                          'TOT_ACTIVOS':'ACTIVO_TOTAL',
                          'UTILILIDAD_PERDIDA': 'UTILILIDAD_OPERACIONAL',
                          'VENTAS' : 'INGRESOS_ACTIVIDAD_ORDINARIA',
                          'TOT_PASIVO': 'PASIVO_TOTAL',
                          'UTILILIDAD_BRUTA': 'RESULTADO_PERIODO',
                          'MAT_REN' : 'MATRICULA_RENOVACION'}, 
                 inplace=True)

In [4]:
# Se separa la fecha para facilitar el análisis
df[['FECHA_MATRICULA_RENOVACION','HORA_FECHA_MAT_REN']] =  df.FECHA_MATRICULA_RENOVACION_HORA.str.split(' ', n=1, expand=True)
# Se separa día, mes y año para facilitar el análisis
df[['DIA','MES', 'ANO']] =  df.FECHA_MATRICULA_RENOVACION.str.split('/', n=2, expand=True)
#Se convierte la variable FECHA_MATRICULA_RENOVACION_HORA en datetime para facilitar manupulación de los datos
df.FECHA_MATRICULA_RENOVACION_HORA = pd.to_datetime(df.FECHA_MATRICULA_RENOVACION_HORA)

In [5]:
#Se organiza el DataFrame según la fecha del movimiento registrado. Esto facilitará las particiones que se harán de la base de datos
df=df.sort_values('FECHA_MATRICULA_RENOVACION_HORA')
print(df.info())
df.head(2)

<class 'pandas.core.frame.DataFrame'>
Int64Index: 123590 entries, 86046 to 6068
Data columns (total 39 columns):
 #   Column                           Non-Null Count   Dtype         
---  ------                           --------------   -----         
 0   MATRICULA                        123590 non-null  object        
 1   NIT                              123590 non-null  object        
 2   CONSECUTIVO_PROPIETARIO          123548 non-null  float64       
 3   MATRICULA_RENOVACION             123590 non-null  object        
 4   ESTADO_MAT_REN                   123590 non-null  object        
 5   ESTADO_ACTUAL                    123590 non-null  object        
 6   RAZON_SOCIAL                     123585 non-null  object        
 7   SECTOR                           123590 non-null  object        
 8   CODIGO_CIIU                      123590 non-null  object        
 9   DESC_CIIU                        123590 non-null  object        
 10  NOM_ENTE_JURIDICO                123590 no

MATRICULA        NIT  CONSECUTIVO_PROPIETARIO MATRICULA_RENOVACION  \
86046   1039875  901251283                      0.0            Matricula   
85978   1039822   31449822                      0.0            Matricula   

      ESTADO_MAT_REN ESTADO_ACTUAL  \
86046              A        ACTIVO   
85978              A        ACTIVO   

                                            RAZON_SOCIAL SECTOR CODIGO_CIIU  \
86046  SERVITEC ELEVADORES S.A.S.                    ...      F        4329   
85978  AYALA RIVERA ADRIANA                          ...      G        4771   

                                               DESC_CIIU  \
86046  OTRAS INSTALACIONES ESPECIALIZADAS            ...   
85978  COMERCIO AL POR MENOR DE PRENDAS DE VESTIR Y S...   

                                       NOM_ENTE_JURIDICO             PN_PJ  \
86046  Sociedad por Acciones Simplificada            ...  Persona jurídica   
85978  Persona Natural                               ...   Persona natural   

      DESC_TAMANO TAMANO957 CIUDAD ULTIMO_ANO_RENOVADO FECHA_MATRICULA  \
86046       MICRO     MICRO   Cali                2019      2019-02-01   
85978       MICRO     MICRO   Cali                2020      2019-02-01   

      FECHA_MATRICULA_RENOVACION_HORA                   EMAIL      TELEFONO  \
86046                      2019-01-02  sharelly1927@gmail.com  3.126583e+09   
85978                      2019-01-02   aa.paloma@hotmail.com  3.207577e+09   

           BARRIO     COMUNA  \
86046  Las Ceibas  Comuna 07   
85978     El Lido  Comuna 19   

                                     DIRECCION_COMERCIAL  \
86046  CRA 7 P BIS # 63 73                           ...   
85978  CL 1 # 47 - 07 LC 12                          ...   

                            REP_LEGAL AFILIADO  PORCENT_EXTRANJERO  \
86046  SHARELLY  PAYAN ERAZO                 N                 0.0   
85978  ADRIANA AYALA RIVERA                  N                 NaN   

       PATRIMONIO  PERSONAL_OCUPADO  ACTIVO_TOTAL  UTILILIDAD_OPERACIONAL  \
86046     1000000               0.0       1000000                     NaN   
85978     1000000               0.0       1000000                     NaN   

       INGRESOS_ACTIVIDAD_ORDINARIA  PASIVO_TOTAL  RESULTADO_PERIODO  \
86046                           NaN             0                NaN   
85978                           NaN             0                NaN   

       ESTABLECIMIENTOS FECHA_MATRICULA_RENOVACION HORA_FECHA_MAT_REN DIA MES  \
86046                 0                  1/02/2019      12:00:00 a.m.   1  02   
85978                 1                  1/02/2019      12:00:00 a.m.   1  02   

        ANO  
86046  2019  
85978  2019

In [6]:
df.groupby('ESTADO_MAT_REN').nunique()

MATRICULA    NIT  CONSECUTIVO_PROPIETARIO  \
ESTADO_MAT_REN                                              
A                   47287  47196                        1   
D                   65122  65121                        1   
R                     101    101                        1   

                MATRICULA_RENOVACION  ESTADO_MAT_REN  ESTADO_ACTUAL  \
ESTADO_MAT_REN                                                        
A                                  2               1              2   
D                                  2               1              2   
R                                  2               1              2   

                RAZON_SOCIAL  SECTOR  CODIGO_CIIU  DESC_CIIU  \
ESTADO_MAT_REN                                                 
A                      47219      20          446        850   
D                      65098      20          444       1114   
R                        101      15           55         60   

                NOM_ENTE_JURIDICO  PN_PJ  DESC_TAMANO  TAMANO957  CIUDAD  \
ESTADO_MAT_REN                                                             
A                              11      2            4          4       7   
D                              11      2            4          4       6   
R                               7      2            4          3       3   

                ULTIMO_ANO_RENOVADO  FECHA_MATRICULA  \
ESTADO_MAT_REN                                         
A                                 4             5654   
D                                 7             8328   
R                                 4               92   

                FECHA_MATRICULA_RENOVACION_HORA  EMAIL  TELEFONO  BARRIO  \
ESTADO_MAT_REN                                                             
A                                         26528  45049     44487     470   
D                                         53362  59858     59715     474   
R                                           123    100        99      75   

                COMUNA  DIRECCION_COMERCIAL  REP_LEGAL  AFILIADO  \
ESTADO_MAT_REN                                                     
A                   46                46433      45942         2   
D                   46                60727      61355         2   
R                   24                  100        100         2   

                PORCENT_EXTRANJERO  PATRIMONIO  PERSONAL_OCUPADO  \
ESTADO_MAT_REN                                                     
A                               16        4993               104   
D                               56       17874               453   
R                                1          42                15   

                ACTIVO_TOTAL  UTILILIDAD_OPERACIONAL  \
ESTADO_MAT_REN                                         
A                       5151                    4461   
D                      20108                   19180   
R                         44                      27   

                INGRESOS_ACTIVIDAD_ORDINARIA  PASIVO_TOTAL  RESULTADO_PERIODO  \
ESTADO_MAT_REN                                                                  
A                                       4202          3771               4586   
D                                      18360         17487              19485   
R                                         26            25                 25   

                ESTABLECIMIENTOS  FECHA_MATRICULA_RENOVACION  \
ESTADO_MAT_REN                                                 
A                             10                         302   
D                             30                         314   
R                              3                          57   

                HORA_FECHA_MAT_REN  DIA  MES  ANO  
ESTADO_MAT_REN                                     
A                            18824   31   12    1  
D                            29167   31   12    1  
R                              120   28   11    1

In [7]:
# Siguiendo las indicaciones de Sistemas y Registro se deben eliminar las filas de las empresas que registren en el ESTADO_MAT_REN la letra R ya que estos movimientos fueron anulados por alguna acción legal. En la mayoría de los casos se anulan las renovaciones por motivo de cancelación hechas antes del 31 de marzo de cada año ya que la ley permite que las empresas cancelen su registro sin pagar la renovación solo si se realiza el proceso antes del 31 de marzo de cda año
df = df[df.ESTADO_MAT_REN != 'R']

In [8]:
# Para obtener los duplicados EXCEPTO la primera observación revisando todas las columnas 
duplicados = df[df.duplicated()]
print('El número de registros duplicados con todas las columnas iguales son:')
print (duplicados.MATRICULA.count())

El número de registros duplicados con todas las columnas iguales son:
0


In [9]:
# Para obtener los duplicados EXCEPTO la última observación revisando la columna Matriculados. Es decir, se tomarán todas las matriculas duplicadas excepto la que registró la ultima modificación 
duplicadosMAT = df[df.duplicated(['MATRICULA'], keep='last')]
print("El número de Matriculas duplicadas es:", duplicadosMAT.MATRICULA.count(), sep='\n')

El número de Matriculas duplicadas es:
21196


In [10]:
# Para obtener los duplicados EXCEPTO la última observación revisando en simultaneo las columnas Matriculados y MATRICULA_RENOVACION. Es decir, se tomarán todas las matriculas duplicadas tanto con su Nnúmero de matricula como lo que hayan hecho en ese año, es decir, si presentó dos renovaciones o dos matriculas se tomarán en la subase creada. Es necesario acalarar que lo anterior se hace exceptuando la que registró la ultima modificación. Esto puede ocurrir debido a que los tramites de renovación de alguna empresa estuveiron mal y se tradaron más del plazo para entregar sus papeles así que se registra una nueva fecha de renovación sin eliminar la primera.
duplicadosMAT_REN = df[df.duplicated(['MATRICULA', 'MATRICULA_RENOVACION'], keep='last')]
print("El número de filas duplicadas analizando dos columnas es:", duplicadosMAT_REN.MATRICULA.count(), sep='\n')

El número de filas duplicadas analizando dos columnas es:
438


In [11]:
# Antes de partir la base de datos. Se hace un conteo para saber cuantas Matriculas y Renovaciones se tienen en la base sin eliminar duplicados
df.MATRICULA_RENOVACION.value_counts()

Renovacion    102703
Matricula      20762
Name: MATRICULA_RENOVACION, dtype: int64

In [12]:
# Ahora es necesario partir la base de datos en dos para hacer la correspondiente limpieza. Se requieren tratar las empresas Matriculadas y Renovadas diferenciadas por su fecha de registro
df_matricula = df.loc[df['MATRICULA_RENOVACION'].isin(['Matricula'])]
df_renovacion = df.loc[df['MATRICULA_RENOVACION'].isin(['Renovacion'])]
print('El número de registros en la BD para Matriculas es:', df_matricula.MATRICULA_RENOVACION.value_counts(), sep='\n')
print('El número de registros en la BD para Renovaciones:', df_renovacion.MATRICULA_RENOVACION.value_counts(), sep='\n')

El número de registros en la BD para Matriculas es:
Matricula    20762
Name: MATRICULA_RENOVACION, dtype: int64
El número de registros en la BD para Renovaciones:
Renovacion    102703
Name: MATRICULA_RENOVACION, dtype: int64


<p>---------------</p>

In [13]:
#aQUÍ DEBE IR EL CODIGO DESPUES DE LIMPIAR EL TEMA DE RENOVACIONES MAS VIEJAS QUE LAS MATRICULAS. SE DEBEN ELIMINAR LAS RENOVACIONES CON FECHAS ANTERIORES A LAS DE LAS MATRICULAS porque esto es un indicador que la empresa hizo un translado de domicilio y se trajo todo su historial a la CCC
#Se convierte la variable FECHA_MATRICULA_RENOVACION_HORA en datetime para facilitar manupulación de los datos
df_renovacion.FECHA_MATRICULA_RENOVACION = pd.to_datetime(df_renovacion.FECHA_MATRICULA_RENOVACION)
df_renovacion = df_renovacion.loc[df_renovacion['FECHA_MATRICULA']<=df_renovacion['FECHA_MATRICULA_RENOVACION']]

In [14]:
# Se organizan las bases según la fecha en la cual se hizo el movimiento corresspondiente a Matricual o Renovación para posterior limpieza. Vale aclarar que esta el ordenamiento es descendente, es decir, se comienza desde 2018/01/01 00:00 hasta 2018/12/31 23:59 (de enero a diciembre)
df_matricula=df_matricula.sort_values('FECHA_MATRICULA_RENOVACION_HORA')
df_renovacion=df_renovacion.sort_values('FECHA_MATRICULA_RENOVACION_HORA')
df_renovacion.head(2)

MATRICULA         NIT  CONSECUTIVO_PROPIETARIO MATRICULA_RENOVACION  \
6758     414087    16764430                      0.0           Renovacion   
62813    983679  1107103275                      0.0           Renovacion   

      ESTADO_MAT_REN ESTADO_ACTUAL  \
6758               D        ACTIVO   
62813              D        ACTIVO   

                                            RAZON_SOCIAL SECTOR CODIGO_CIIU  \
6758   PORTOCARRERO PALENCIA CARLOS DUBAN            ...      S        9522   
62813  SALAZAR HERNANDEZ JUAN PABLO                  ...      G        4769   

                                               DESC_CIIU  \
6758   MANTENIMIENTO Y REPARACIÓN DE APARATOS Y EQUIP...   
62813  COMERCIO AL POR MENOR DE OTROS ARTÍCULOS CULTU...   

                                       NOM_ENTE_JURIDICO            PN_PJ  \
6758   Persona Natural                               ...  Persona natural   
62813  Persona Natural                               ...  Persona natural   

      DESC_TAMANO TAMANO957 CIUDAD ULTIMO_ANO_RENOVADO FECHA_MATRICULA  \
6758        MICRO     MICRO   Cali                2020      1995-10-19   
62813       MICRO     MICRO   Cali                2020      2017-04-18   

      FECHA_MATRICULA_RENOVACION_HORA                    EMAIL      TELEFONO  \
6758              2019-01-02 07:45:35       cardupor@gmail.com  4.476960e+06   
62813             2019-01-02 08:00:38  jpablo_1996@hotmail.com  3.106849e+09   

          BARRIO     COMUNA  \
6758      Calima  Comuna 04   
62813  San Pedro  Comuna 03   

                                     DIRECCION_COMERCIAL  \
6758   CL. 68      No.   4     N 64                  ...   
62813  CR 9 # 11 - 50 PISO 2 LOCAL 18 A              ...   

                            REP_LEGAL AFILIADO  PORCENT_EXTRANJERO  \
6758   CARLOS DUBAN PORTOCARRERO PALE        N                 NaN   
62813  JUAN PABLO SALAZAR HERNANDEZ          N                 NaN   

       PATRIMONIO  PERSONAL_OCUPADO  ACTIVO_TOTAL  UTILILIDAD_OPERACIONAL  \
6758      2139000               0.0       2139000               2139000.0   
62813     3000000               1.0       3000000                     0.0   

       INGRESOS_ACTIVIDAD_ORDINARIA  PASIVO_TOTAL  RESULTADO_PERIODO  \
6758                      2139000.0             0          2139000.0   
62813                           0.0             0                0.0   

       ESTABLECIMIENTOS FECHA_MATRICULA_RENOVACION HORA_FECHA_MAT_REN DIA MES  \
6758                  1                 2019-01-02       7:45:35 a.m.   1  02   
62813                 1                 2019-01-02       8:00:38 a.m.   1  02   

        ANO  
6758   2019  
62813  2019

In [15]:
# Se procede a eliminar los duplicados en las dos bases y la idea es dejar el último movimiento registrado. Esto se debe gracias a que se identificó que algunas empresas registran algun movimiento y por algun motivo este es devuelto, en la mayoría de los casos la corrección sugerida es hecha en el plazo para mantener la fecha inicial del movimiento, sin embargo, cuando la empresa deja pasar este plazo máximo se debe generar un nuevo movimiento lo cual genera duplicados en la información
df2_matricula=df_matricula.sort_values('FECHA_MATRICULA_RENOVACION_HORA').drop_duplicates('MATRICULA', keep='last')
df2_renovacion=df_renovacion.sort_values('FECHA_MATRICULA_RENOVACION_HORA').drop_duplicates('MATRICULA', keep='last')

In [16]:
# Una vez eliminados lo duplicados se cuenta el número de resgitros 
print('El número de registros en la BD para Matriculas después de eliminar duplicados es:', df2_matricula.MATRICULA_RENOVACION.value_counts(), sep='\n')
print('El número de registros en la BD para Renovaciones después de eliminar duplicados es:', df2_renovacion.MATRICULA_RENOVACION.value_counts(), sep='\n')

El número de registros en la BD para Matriculas después de eliminar duplicados es:
Matricula    20759
Name: MATRICULA_RENOVACION, dtype: int64
El número de registros en la BD para Renovaciones después de eliminar duplicados es:
Renovacion    98823
Name: MATRICULA_RENOVACION, dtype: int64


In [17]:
# Se procede a unir las bases de datos para la posterior limpieza en conjunto
df2 = pd.concat([df2_matricula, df2_renovacion])
df2 = df2.sort_values('MATRICULA_RENOVACION', ascending=True)
print('El número de registros en la BD unida es:', df2.MATRICULA_RENOVACION.value_counts(), sep='\n')

El número de registros en la BD unida es:
Renovacion    98823
Matricula     20759
Name: MATRICULA_RENOVACION, dtype: int64


In [18]:
df2.head(2)

MATRICULA         NIT  CONSECUTIVO_PROPIETARIO MATRICULA_RENOVACION  \
86046    1039875   901251283                      0.0            Matricula   
110499   1060600  1130604628                      0.0            Matricula   

       ESTADO_MAT_REN ESTADO_ACTUAL  \
86046               A        ACTIVO   
110499              A        ACTIVO   

                                             RAZON_SOCIAL SECTOR CODIGO_CIIU  \
86046   SERVITEC ELEVADORES S.A.S.                    ...      F        4329   
110499  VILLARRAGA ACOSTA DIBISAY                     ...      G        4711   

                                                DESC_CIIU  \
86046   OTRAS INSTALACIONES ESPECIALIZADAS            ...   
110499  COMERCIO AL POR MENOR EN ESTABLECIMIENTOS NO E...   

                                        NOM_ENTE_JURIDICO             PN_PJ  \
86046   Sociedad por Acciones Simplificada            ...  Persona jurídica   
110499  Persona Natural                               ...   Persona natural   

       DESC_TAMANO TAMANO957 CIUDAD ULTIMO_ANO_RENOVADO FECHA_MATRICULA  \
86046        MICRO     MICRO   Cali                2019      2019-02-01   
110499       MICRO     MICRO   Cali                2019      2019-08-13   

       FECHA_MATRICULA_RENOVACION_HORA                   EMAIL      TELEFONO  \
86046                       2019-01-02  sharelly1927@gmail.com  3.126583e+09   
110499                      2019-08-13  denisser12@hotmail.com  3.184202e+09   

            BARRIO     COMUNA  \
86046   Las Ceibas  Comuna 07   
110499         NaN        NaN   

                                      DIRECCION_COMERCIAL  \
86046   CRA 7 P BIS # 63 73                           ...   
110499  CRA 42C  NO. 49   42  B/ CIUDAD CORDOBA       ...   

                             REP_LEGAL AFILIADO  PORCENT_EXTRANJERO  \
86046   SHARELLY  PAYAN ERAZO                 N                 0.0   
110499  DIBISAY VILLARRAGA ACOSTA             N                 NaN   

        PATRIMONIO  PERSONAL_OCUPADO  ACTIVO_TOTAL  UTILILIDAD_OPERACIONAL  \
86046      1000000               0.0       1000000                     NaN   
110499     1000000               0.0       1000000                     0.0   

        INGRESOS_ACTIVIDAD_ORDINARIA  PASIVO_TOTAL  RESULTADO_PERIODO  \
86046                            NaN             0                NaN   
110499                           0.0             0                0.0   

        ESTABLECIMIENTOS FECHA_MATRICULA_RENOVACION HORA_FECHA_MAT_REN DIA  \
86046                  0                  1/02/2019      12:00:00 a.m.   1   
110499                 1                 13/08/2019      12:00:00 a.m.  13   

       MES   ANO  
86046   02  2019  
110499  08  2019

In [19]:
# Para eliminar duplicados se debe tener en cuenta que en Matricula nos interesa dejar el primer registro que tengamos en la base pues por cada matricula se genera una renovación
df3 = df2.sort_values('MATRICULA_RENOVACION', ascending=True).drop_duplicates('MATRICULA', keep='first')
print('El número de registros en la BD unida sin duplicados es:', df3.MATRICULA_RENOVACION.value_counts(), sep='\n')

El número de registros en la BD unida sin duplicados es:
Renovacion    81466
Matricula     20759
Name: MATRICULA_RENOVACION, dtype: int64


In [20]:
df3.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 102225 entries, 86046 to 6068
Data columns (total 39 columns):
 #   Column                           Non-Null Count   Dtype         
---  ------                           --------------   -----         
 0   MATRICULA                        102225 non-null  object        
 1   NIT                              102225 non-null  object        
 2   CONSECUTIVO_PROPIETARIO          102185 non-null  float64       
 3   MATRICULA_RENOVACION             102225 non-null  object        
 4   ESTADO_MAT_REN                   102225 non-null  object        
 5   ESTADO_ACTUAL                    102225 non-null  object        
 6   RAZON_SOCIAL                     102221 non-null  object        
 7   SECTOR                           102225 non-null  object        
 8   CODIGO_CIIU                      102225 non-null  object        
 9   DESC_CIIU                        102225 non-null  object        
 10  NOM_ENTE_JURIDICO                102225 no

In [21]:
# Se procede a graficar las distribuciones según el tratamiento (limpia y sin limpiar)
fig = go.Figure()
fig.add_trace(go.Histogram(histfunc="sum", y=df.MATRICULA_RENOVACION, name="Sin limpiar"))
fig.add_trace(go.Histogram(histfunc="count", y=df3.MATRICULA_RENOVACION , name="limpia"))
fig.update_layout(
    title_text='Número total de registros por Matricula o Renovación', # title of plot
    xaxis_title_text='Número de registros', # xaxis label
    yaxis_title_text=None, # yaxis label
    bargap=0.2, # gap between bars of adjacent location coordinates
    bargroupgap=0.1 # gap between bars of the same location coordinates
)

# Además se agrega un gráfico de distribución según Ente Juridíco
fig2 = go.Figure(px.histogram(df3, x='MATRICULA_RENOVACION', color='PN_PJ', title='Número total de registros por Matricula o Renovación según Ente Jurídico', color_discrete_sequence=px.colors.qualitative.Alphabet))


fig.show()
fig2.show()

<p> Desde aquí se inicia la limpieza de otras variables para facilitar los posteriores análisis</p>

In [22]:
df3.groupby('CIUDAD')['MATRICULA'].nunique()

CIUDAD
Cali         93274
Dagua          847
Jamundi       3812
La Cumbre      255
Palmira          2
Vijes          211
Yumbo         3818
Name: MATRICULA, dtype: int64

In [23]:
# En esta línea de código se limpian los diferentes valores de Comuna que se tienen
df3.COMUNA.replace(to_replace =["Comuna 01", "Comuna 02", "Comuna 03", "Comuna 04", "Comuna 05", "Comuna 06", "Comuna 07", "Comuna 08", "Comuna 09"],  
                            value =["Comuna 1", "Comuna 2", "Comuna 3", "Comuna 4", "Comuna 5", "Comuna 6", "Comuna 7", "Comuna 8", "Comuna 9"], inplace=True)
# En esta línea se reemplazan las comunas con nombre de municipio por el nombre del municipio
df3.COMUNA.replace(to_replace =["Comuna Dagua", "Comuna Jamundi", "Comuna La Cumbre", "Comuna Vijes", "Comuna Yumbo"],  
                            value =["Dagua", "Jamundi", "La Cumbre", "Vijes", "Yumbo"], inplace=True) 
# En esta línea se reemplazan las ciudades diferentes a la jurisdicción de la CC por Cali para facilitar el análisis
df3.CIUDAD.replace(to_replace =["Bogota", "Palmira", "Piendamo", "Calima Darien", "Sevilla"],  
                            value ="Cali", inplace=True)
df3.groupby('CIUDAD')['MATRICULA'].nunique()

CIUDAD
Cali         93276
Dagua          847
Jamundi       3812
La Cumbre      255
Vijes          211
Yumbo         3818
Name: MATRICULA, dtype: int64

In [24]:
#Se crea el dicccionario de datos con las varaibles correspondientes para cruzar con la base de datoslimpia de Registro Mercantil. Este diccionario fue creado por el grupo de Estudios Económico de la Cámara de Comercio de Cali evidenciando las diferentes maneras de declarr los barrios por parte de los empresarios. No obstante, este ejercicio deberá ser retroalimentado constantemente para enriquecer el análisis de los datos

dict_barrios = {
    'BARRIO_REG': ["La Legua","Palermo","Terron Colorado","Vista Hermosa","Sector Patio Bonito","Aguacatal","Alto Aguacatal","Bajo Aguacatal-Las Colinas","Santa Rita","Santa Teresita","Arboledas","Normandia","Juanambu","Centenario","Granada","Versalles","San Vicente","Prados Del Norte (N Sn Vic.)","La Flora","Area Libre-Parque Del Amor","La Campina","La Paz","La Paz (Cabecera)","El Bosque","Menga","Ciudad Los Alamos","Chipichape","Brisas De Los Alamos","Urbanizacion La Merced","Vipasa","Urbanizacion La Flora","Altos De Menga","Altos De Normandia","Altos Santa Monica","El Filo","Golondrinas (Cabecera)","La Maria","San Isidro","Sector Altos Normandia-Bataclan","El Nacional","El Penon","Acueducto San Antonio","San Antonio","San Cayetano","Los Libertadores","San Juan Bosco","Santa Rosa","La Merced","San Pascual","El Calvario","San Pedro","San Nicolas","El Hoyo","El Piloto","Jorge Isaacs","Santander","Porvenir","San Francisco","Las Delicias","Manzanares","Salomia","Fatima","Ignacio Rengifo","Guillermo Valencia","La Isla","Marco Fidel Suarez","Evaristo Garcia","La Esmeralda","Bolivariano","Olaya Herrera","Unidad Res.Bueno Madrid","Flora Industrial","Calima","Sector Calima-La 14","Industria De Licores","La Alianza","El Sena","Los Andes","Los Guayacanes","Chiminangos Segunda Etapa","Chiminangos Primera Etapa","Metropolitano Del Norte","Villa Del Sol","Paseo De Los Almendros","Torres De Comfandi","San Luis","Jorge Eliecer Gaitan","Paso Del Comercio (El Carm)","Los Alcazares","Petecuy Primera Etapa","Petecuy Segunda Etapa","La Rivera Primera Etapa","Los Guaduales","Petecuy Tercera Etapa","Ciudadela Floralia","Fonaviemcali","San Luis Ii","Urbanizacion Calimio","Sector Puente Del Comercio","Alfonso Lopez 1 Etapa","Alfonso Lopez 2 Etapa","Alfonso Lopez 3 Etapa","Puerto Nuevo","Puerto Mallarino","Urb.Angel Del Hogar (A.San)","Siete De Agosto","Los Pinos","San Marino","Las Ceibas","Base Aerea","Parque De La Cana","Fepicol","Primitivo Crespo","Simon Bolivar","Saavedra Galindo","Rafael Uribe Uribe","Uribe Uribe","Santa Monica Popular","La Floresta","Benjamin Herrera","Municipal","Industrial","El Troncal","Las Americas","Atanasio Girardot","Santa Fe","Chapinero","Villa Colombia","El Trebol","La Base","Planta De Tratam.Y Taller","Alameda","Bretana","Junin","Santa Anita La Selva","Guayaquil","Aranjuez","Manuel Maria Buenaventura","Santa Monica Belalcazar","Belalcazar","Sucre","Barrio Obrero","El Dorado","El Guabal","La Libertad","Santa Elena","Las Acacias","Santo Domingo","Jorge Zawadsky","Olimpico","Cristobal Colon","La Selva","Barrio Departamental","Pasoancho","Panamericano","Colseguros Andes","San Cristobal","Las Granjas","San Judas Tadeo","San Judas Tadeo I","San Judas Tadeo Ii","Barrio San Carlos","Maracaibo","Ciudad Modelo","La Independencia","La Esperanza","Urbanizacion Boyaca","El Jardin","La Fortaleza","El Recuerdo","Aguablanca","El Prado","20 De Julio","Prados De Oriente","Villa Del Sur","Jose Holguin Garces","Leon Xiii","Jose Maria Cordoba","San Pedro Claver","Los Conquistadores","La Gran Colombia","San Benito","Primavera","Villanueva","Asturias","Eduardo Santos","Barrio Alfonso Barberena A.","El Paraiso","Fenalco Kennedy","Nueva Floresta Del Ict","Julio Rincon","Doce De Octubre","El Rodeo","Sindical","Bello Horizonte","Ulpiano Lloreda","El Vergel","El Poblado I","El Poblado Ii","Los Comuneros Ii Etapa","Ricardo Balcazar","Omar Torrijos","El Diamante","Lleras Restrepo","Villa Del Lago","Los Robles","Rodrigo Lara Bonilla","Charco Azul","Villablanca","Calipso","Calypso","Yira Castro","Lleras","Lleras Cinta Larga","Marroquin Iii","Los Lagos","Sector Laguna Del Pondaje","El Pondaje","Alfonso Bonilla Aragon","Alirio Mora Beltran","Manuela Beltran","Las Orquideas","Marroquin Ii Etapa","Marroquin I Etapa","Puerta Del Sol","Los Naranjos I","Promociones Populares  B","Los Naranjos Ii","El Retiro","Los Comuneros I Etapa","Laureano Gomez","El Vallado","Vallado","Bajos Ciudad Cordoba","Ciudad Cordoba","Mojica","Mariano Ramos","Republica De Israel","Union De Vivienda Popular","Antonio Narino","Brisas Del Limonar","Ciudad 2000","La Alborado","La Playa","Primero De Mayo","Ciudadela Comfandi","Ciudad Universitaria","Bifamiliares El Dorado","Urbanizacion Caney","Lili","El Ingenio","Las Quintas De Don Simon","Ciudad Capri","La Hacienda","Canaverales Los Samanes","El Limonar","Bosques Del Limonar","El Gran Limonar Cataya","El Gran Limonar","Unicentro Cali","Ciudadela Pasoancho","Prados Del Limonar","Urbanizacion San Joaquin","Buenos Aires","Barrio Caldas","Camilo Torres Restrepo","Los Chorros","Batallon Pichincha","Melendez","Los Farallones","Francisco Eladio Ramirez","Prados Del Sur","Horizontes","Mario Correa Rengifo","Lourdes","Colinas Del Sur","Alferez Real","Napoles","El Jordan","Cuarteles Napoles","Sector Alto De Los Chorros","Alto Melendez-Polvorines","Sector Melendez","Sector Alto Jordan","Alto Napoles","El Refugio","La Cascada","El Lido","Urbanizacion Tequendama","Barrio Eucaristico","U.D.Panamericana-Ant.Hipodromo","U.Dep.Panamericana","San Fernando Nuevo","Urbanizacion Nueva Granada","Santa Isabel","Bellavista","San Fernando Viejo","Miraflores","3 De Julio","El Cedro","Champagnat","Urbanizacion Colseguros","Los Cambulos","El Mortinal","Urbanizacion Militar","Cuarto De Legua Guadalupe","Cuarto De Lugua-Guadalupe","Nueva Tequendama","Camino Real J.Borrero S.","Camino Real-Joaquin Borrero S.","Santa Barbara","Unid.Res.Santiago De Cali","Camino Real Los Fundadores","Camino Real-Los Fundadores","Canaveralejo Seguros Patria","Canaveral","Pampa Linda","Sector Canaveralejo Guadalupe","Sector Bosque Municipal","El Cortijo","Belisario Caicedo","Sector Canaveralejo Sur La Sirena","Siloe","Lleras Camargo","Belen","Urbanizacion Santa Helena","Brisas De Mayo","Tierra Blanca","Pueblo Joven","Cementerio -Carabineros","Parcelacion Monaco La Sultana","Pizamos I","Pizamos Ii","Calimio Desepaz","El Remanso","Los Lideres","Desepaz Invicali","Compartir","Ciudad Talanga","Potrero Grande","Ciudadela Del Rio - Cvc","Valle Grande","Planta De Tratamiento","Urbanizacion Ciudad Jadin","Urbanizacion Ciudad Jardin","Parcelaciones Pance","Urbanizacion Rio Lili","Ciudad Campestre","Club Campestre","Bella Vista","Bolivar","Brisas Del Rio","Barrio Dagua","Cascajal","Cauca Seco","Club Canasgordas","Comfenalco Sede Recreativa","El Boqueron","El Homiguero ( Cabecera)","Hacienda Las Vegas","Parcelacion Andalucia","Parcelaciones El Hormiguero","Piedra Grande","El Saladito (Cabecera)","San Miguel","San Pablo","Cabanas De Carvajal","Felidia (Cabecera)","Las Nieves","Santa Helena","Fray Pena","Barrio Jamundi","Juan Pablo Ii","Alto De Los Mangos","Alto Del Cerro","Anchicaya","Bella Suiza","Campo Alegre","Campoalegre","El Crucero","El Rosario","La Buitrera (Cabecera)","La Luisa","La Riverita","La Sirena","Las Palmas-El Portento-Girasoles","Los Cerros","Parcelaciones Altos Cerros","Parcelaciones Bajos Cerros","Pueblo Nuevo","Sector La Luisa","Sector La Luisa-La Sirena","Sector Las Neblinas","La Castilla (Cabecera)","Las Palmas","Los Limones","Montanitas","La Cumbre","Kilometro 18 (Via Al Mar)","La Elvira (Cabecera)","La Leonera (Cabecera)","La Nueva Estancia","Bajo Cristo Rey-Brisas De Los Cristales","Cerro De Cristo Rey","El Cabuyal","El Mameyal","Los Andes (Cabecera)","Los Andes Parte Baja","Los Mangos","Monaco","Los Andes B-La Riviera-El Saman","Los Parques-Barranquilla","Los Portales Nuevo Rey","Las Vegas","Mayapan Las Vegas","Cinturon  Ecologico","Madre Vieja Rio Cauca","Navarro (Cabecera)","Navarro-La Chanca","Nuevo Orizonte","Area Libre Rios Pance-Jamundi","Cementerio Metropolitano Del Sur","Comfandi Sede Recreativa","Corredor Cali-Jamundi","El Banqueo","El Porvenir","El Trueno","La Castellana","La Voragine","Pance (Cabecera)","Parcelacion Chorro De Plata","Parcelaciones Cerros Pance","Parcelaciones Pance Zona Plana","Panorama","Penas Blancas","Pichinde (Cabecera)","Pizamos Iii - Las Dalias","Popular","Puerto Isaac","San Jorge","Santa Monica","Sect.Asprosocial-Diamante","Sultana-Berlin","Tejares Cristales","Trinidad","Trinidad I","U.Dep.A.Galindo Plaza Toros","Urbanizacion Canaveralejo","Venezuela-Urb. Canaveralejo","Barrio Vijes","Villa Del Prado-El Guabito","La Fonda","Los Mangos (Parte Baja)","Villacarmelo (Cabecera)","Villamercedes I-Villa Luz-Las Garzas","Barrio Yumbo","Imviyumbo San Jorge","ACOPI","FELIDIA","GOLONDRINAS","HORMIGUERO","LA BUITRERA","LA CASTILLA","LA ELVIRA","LA LEONERA","MONTE BELLO","MONTEBELLO","MONTEBELLO (CABECERA)","NAVARRO","PANCE","PICHINDE","SALADITO"],

        'NOM_BAR': ["Terrón Colorado",	"Terrón Colorado",	"Terrón Colorado",	"Vista Hermosa",	"Sector Patio Bonito",	"Aguacatal",	"Aguacatal",	"Aguacatal",	"Santa Rita",	"Santa Teresita",	"Arboledas",	"Normandía",	"Juanambú",	"Centenario",	"Granada",	"Versalles",	"San Vicente",	"Prados del Norte",	"La Flora",	"La Flora",	"La Campiña",	"La Paz",	"La Paz",	"El Bosque",	"Menga",	"Ciudad Los Alamos",	"Chipichape",	"Brisas de los Alamos",	"Urbanización La Merced",	"Vipasa",	"Urbanización La Flora",	"Altos de Menga",	"Golondrinas",	"Golondrinas",	"Golondrinas",	"Golondrinas",	"Golondrinas",	"Golondrinas",	"Golondrinas",	"El Nacional",	"El Peñón",	"San Antonio",	"San Antonio",	"San Cayetano",	"Los Libertadores",	"San Juan Bosco",	"Santa Rosa",	"La Merced",	"San Pascual",	"El Calvario",	"San Pedro",	"San Nicolas",	"El Hoyo",	"El Piloto",	"Jorge Isaacs",	"Santander",	"Porvenir",	"Porvenir",	"Las Delicias",	"Manzanares",	"Salomia",	"Fátima",	"Ignacio Rengifo",	"Guillermo Valencia",	"La Isla",	"Marco Fidel Suárez",	"Evaristo García",	"La Esmeralda",	"Bolivariano",	"Olaya Herrera",	"Unidad Residencial Bueno Madrid",	"Flora Industrial",	"Calima",	"Calima",	"Industria de Licores",	"La Alianza",	"El Sena",	"Los Andes",	"Los Guayacanes",	"Chiminangos Segunda Etapa",	"Chiminangos Primera Etapa",	"Metropolitano del Norte",	"Villa del Sol",	"Paseo de Los Almendros",	"Torres de Comfandi",	"San Luís",	"Jorge Eliecer Gaitán",	"Paso del Comercio",	"Los Alcázares",	"Petecuy Primera Etapa",	"Petecuy Segunda Etapa",	"La Rivera Primera Etapa",	"Los Guaduales",	"Petecuy Tercera Etapa",	"Ciudadela Floralia",	"Fonaviemcali",	"San Luís II",	"Urbanización Calimio",	"Sector Puente del Comercio",	"Alfonso López P. 1a. Etapa",	"Alfonso López P. 2a. Etapa",	"Alfonso López P. 3a. Etapa",	"Puerto Nuevo",	"Puerto Mallarino",	"Urbanización El Angel del Hogar",	"Siete de Agosto",	"Los Pinos",	"San Marino",	"Las Ceibas",	"Base Aérea",	"Parque de la Caña",	"Fepicol",	"Primitivo Crespo",	"Simón Bolívar",	"Saavedra Galindo",	"Uribe Uribe",	"Uribe Uribe",	"Santa Mónica Popular",	"La Floresta",	"Benjamín Herrera",	"Municipal",	"Industrial",	"El Troncal",	"Las Américas",	"Atanasio Girardot",	"Santa Fe",	"Chapinero",	"Villa Colombia",	"EL Trébol",	"La Base",	"La Base",	"Alameda",	"Bretaña",	"Junín",	"Junín",	"Guayaquil",	"Aranjuez",	"Manuel María Buenaventura",	"Santa Mónica Belalcázar",	"Belalcázar",	"Sucre",	"Barrio Obrero",	"El Dorado",	"El Guabal",	"La Libertad",	"Santa Elena",	"Las Acacias",	"Santo Domingo",	"Jorge Zawadsky",	"Olímpico",	"Cristóbal Colón",	"La Selva",	"Barrio Departamental",	"Pasoancho",	"Panamericano",	"Colseguros Andes",	"San Cristobal",	"Las Granjas",	"San Judas Tadeo I Etapa",	"San Judas Tadeo I Etapa",	"San Judas Tadeo II Etapa",	"San Carlos",	"Maracaibo",	"La Independencia",	"La Independencia",	"La Esperanza",	"Urbanización Boyacá",	"El Jardín",	"La Fortaleza",	"El Recuerdo",	"Aguablanca",	"El Prado",	"20 de Julio",	"Prados de Oriente",	"Villa del Sur",	"José Holguín Garcés",	"León XIII",	"José María Cordoba",	"San Pedro Claver",	"Los Conquistadores",	"La Gran Colombia",	"San Benito",	"Primavera",	"Villanueva",	"Asturias",	"Eduardo Santos",	"Alfonso Barberena A.",	"El Paraiso",	"Fenalco Kennedy",	"Nueva Floresta",	"Julio Rincón",	"Doce de Octubre",	"El Rodeo",	"Sindical",	"Bello Horizonte",	"Ulpiano Lloreda",	"El Vergel",	"El Poblado I",	"El Poblado II",	"Los Comuneros Segunda Etapa",	"Ricardo Balcázar",	"Omar Torrijos",	"El Diamante",	"Lleras Restrepo",	"Villa del Lago",	"Los Robles",	"Rodrigo Lara Bonilla",	"Charco Azul",	"Villablanca",	"Calipso",	"Calipso",	"Yira Castro",	"Lleras Restrepo II Etapa",	"Lleras Restrepo II Etapa",	"Marroquín III",	"Los Lagos",	"Sector Laguna del Pondaje",	"El Pondaje",	"Alfonso Bonilla Aragón",	"Alirio Mora Beltrán",	"Manuela Beltrán",	"Las Orquídeas",	"Marroquín II Etapa",	"Marroquín I Etapa",	"Puerta del Sol",	"Los Naranjos I",	"Promociones Populares B",	"Los Naranjos II",	"El Retiro",	"Comuneros I",	"Laureano Gómez",	"El Vallado",	"El Vallado",	"Ciudad Cordoba",	"Ciudad Cordoba",	"Mojica",	"Mariano Ramos",	"República de Israel",	"Unión de Vivienda Popular",	"Antonio Nariño",	"Brisas del Limonar",	"Ciudad 2000",	"La Alborada",	"La Playa",	"Primero De Mayo",	"Ciudadela Comfandi",	"Ciudad Universitaria",	"Caney",	"Caney",	"Lili",	"El Ingenio",	"Las Quintas de Don Simón",	"Ciudad Capri",	"La Hacienda",	"Cañaverales - Los Samanes",	"El Limonar",	"Bosques del Limonar",	"El Gran Limonar - Cataya",	"El Gran Limonar",	"Unicentro Cali",	"Ciudadela Pasoancho",	"Prados del Limonar",	"Urbanización San Joaquin",	"Buenos Aires",	"Barrio Caldas",	"Barrio Caldas",	"Los Chorros",	"Meléndez",	"Meléndez",	"Los Farallones",	"Francisco Eladio Ramirez",	"Prados del Sur",	"Horizontes",	"Mario Correa Rengifo",	"Lourdes",	"Colinas del Sur",	"Alférez Real",	"Nápoles",	"El Jordán",	"Cuarteles Napoles",	"Sector Alto de Los Chorros",	"Polvorines",	"Sector Meléndez",	"Sector Alto Jordán",	"Alto Nápoles ",	"El Refugio",	"La Cascada",	"El Lido",	"Urbanización Tequendama",	"Barrio Eucarístico",	"Barrio Eucarístico",	"Barrio Eucarístico",	"San Fernando Nuevo",	"Urbanización Nueva Granada",	"Santa Isabel",	"Bellavista",	"San Fernando Viejo",	"Miraflores",	"3 de Julio",	"El Cedro",	"Champagñat",	"Urbanización Colseguros",	"Los Cambulos",	"El Mortiñal",	"Urbanización Militar",	"Cuarto de Legua - Guadalupe",	"Cuarto de Legua - Guadalupe",	"Nueva Tequendama ",	"Camino Real - Joaquin Borrero Sinisterra",	"Camino Real - Joaquin Borrero Sinisterra",	"Santa Barbara",	"Unidad Residencial Santiago de Cali",	"Cañaveralejo - Seguros Patria",	"Cañaveralejo - Seguros Patria",	"Cañaveralejo - Seguros Patria",	"Cañaveral",	"Pampa Linda",	"Sector Cañaveralejo Guadalupe",	"Sector Bosque Municipal",	"El Cortijo",	"Belisario Caicedo",	"Belisario Caicedo",	"Siloé",	"Lleras Camargo",	"Belén",	"Belén",	"Brisas de Mayo",	"Tierra Blanca",	"Pueblo Joven",	"Carabineros",	"La Sultana",	"Pízamos I",	"Pízamos II",	"Calimio Desepaz",	"El Remanso",	"Los Líderes",	"Desepaz Invicali",	"Compartir",	"Ciudad Talanga",	"Potrero Grande",	"Ciudadela del Río",	"Valle Grande",	"Planta de Tratamiento",	"Urbanización Ciudad Jardín",	"Urbanización Ciudad Jardín",	"Parcelaciones Pance",	"Urbanización Río Lili",	"Ciudad Campestre",	"Club Campestre",	"Altos de Santa Isabel -  La Morelia",	"Bolívar",	"Brisas Del Río",	"Dagua",	"El Hormiguero",	"El Hormiguero",	"El Hormiguero",	"El Hormiguero",	"El Hormiguero",	"El Hormiguero",	"El Hormiguero",	"El Hormiguero",	"El Hormiguero",	"El Hormiguero",	"El Saladito",	"El Saladito",	"El Saladito",	"Felidia",	"Felidia",	"Felidia",	"Felidia",	"Fray Pena",	"Jamundi",	"Juan Pablo II",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Castilla",	"La Castilla",	"La Castilla",	"La Castilla",	"La Cumbre",	"La Elvira",	"La Elvira",	"La Leonera",	"La Nueva Estancia",	"Los Andes - Corregimiento",	"Los Andes - Corregimiento",	"Los Andes - Corregimiento",	"Los Andes - Corregimiento",	"Los Andes - Corregimiento",	"Los Andes - Corregimiento",	"Los Andes - Corregimiento",	"Los Andes - Corregimiento",	"Los Andes B - La Riviera",	"Los Parques - Barranquilla",	"Los Portales - Nuevo Rey",	"Mayapan - Las Vegas",	"Mayapan - Las Vegas",	"Navarro",	"Navarro",	"Navarro",	"Navarro - La Chanca",	"Nuevo Horizonte",	"Pance",	"Pance",	"Pance",	"Pance",	"Pance",	"Pance",	"Pance",	"Pance",	"Pance",	"Pance",	"Pance",	"Pance",	"Pance",	"Panorama",	"Pichinde",	"Pichinde",	"Pízamos III - Las Dalias",	"Popular",	"Puerto Isaac",	"San Jorge",	"Santa Mónica Popular",	"Sector Asprosocial-Diamante",	"Sultana - Berlín - San Francisco ",	"Tejares - Cristales",	"Trinidad I",	"Trinidad I",	"U.D. Alberto Galindo -  Plaza de Toros",	"Venezuela - Urbanización Cañaveralejo",	"Venezuela - Urbanización Cañaveralejo",	"Vijes",	"Villa del Prado - El Guabito",	"Villacarmelo",	"Villacarmelo",	"Villacarmelo",	"Villamercedes I - Villa Luz - Las Garzas",	"Yumbo",	"Yumbo",	"Acopi",	"Felidia",	"Golondrinas",	"Hormiguero",	"La Buitrera",	"La Castilla",	"La Elvira",	"La Leonera",	"Monte Bello",	"Montebello",	"Montebello",	"Navarro",	"Pance",	"Pichinde",	"Saladito",],

        'COD_BAR': ["0101",	"0101",	"0101",	"0102",	"0196",	"0199",	"0199",	"0199",	"0201",	"0202",	"0203",	"0204",	"0205",	"0206",	"0207",	"0208",	"0209",	"0211",	"0212",	"0212",	"0213",	"0214",	"0214",	"0215",	"0216",	"0217",	"0218",	"0219",	"0293",	"0294",	"0295",	"0296",	"0297",	"0297",	"0297",	"0297",	"0297",	"0297",	"0297",	"0301",	"0302",	"0303",	"0303",	"0304",	"0305",	"0306",	"0307",	"0308",	"0309",	"0310",	"0311",	"0312",	"0313",	"0314",	"0401",	"0402",	"0403",	"0403",	"0404",	"0405",	"0406",	"0407",	"0411",	"0412",	"0413",	"0414",	"0415",	"0416",	"0417",	"0418",	"0419",	"0420",	"0421",	"0421",	"0423",	"0497",	"0501",	"0502",	"0503",	"0504",	"0505",	"0506",	"0595",	"0596",	"0598",	"0601",	"0602",	"0603",	"0604",	"0605",	"0606",	"0607",	"0608",	"0609",	"0610",	"0695",	"0696",	"0697",	"0698",	"0701",	"0702",	"0703",	"0704",	"0705",	"0706",	"0707",	"0708",	"0709",	"0710",	"0711",	"0797",	"0798",	"0801",	"0802",	"0803",	"0804",	"0804",	"0805",	"0806",	"0807",	"0808",	"0809",	"0810",	"0811",	"0812",	"0813",	"0814",	"0815",	"0816",	"0817",	"0817",	"0901",	"0902",	"0903",	"0903",	"0904",	"0905",	"0906",	"0907",	"0908",	"0909",	"0910",	"1001",	"1002",	"1003",	"1004",	"1005",	"1006",	"1007",	"1008",	"1009",	"1010",	"1011",	"1012",	"1013",	"1014",	"1015",	"1016",	"1017",	"1017",	"1018",	"1101",	"1102",	"1103",	"1103",	"1104",	"1105",	"1106",	"1107",	"1108",	"1109",	"1110",	"1111",	"1112",	"1114",	"1115",	"1116",	"1117",	"1118",	"1119",	"1120",	"1121",	"1122",	"1201",	"1202",	"1203",	"1204",	"1205",	"1206",	"1207",	"1208",	"1209",	"1210",	"1211",	"1212",	"1301",	"1302",	"1303",	"1304",	"1305",	"1306",	"1307",	"1308",	"1309",	"1310",	"1311",	"1312",	"1313",	"1314",	"1315",	"1315",	"1390",	"1393",	"1393",	"1394",	"1395",	"1397",	"1398",	"1401",	"1402",	"1403",	"1404",	"1405",	"1406",	"1495",	"1496",	"1498",	"1499",	"1501",	"1502",	"1503",	"1504",	"1504",	"1596",	"1596",	"1598",	"1601",	"1602",	"1603",	"1604",	"1605",	"1697",	"1698",	"1701",	"1702",	"1703",	"1705",	"1774",	"1774",	"1775",	"1780",	"1782",	"1783",	"1784",	"1786",	"1787",	"1788",	"1789",	"1790",	"1791",	"1793",	"1794",	"1796",	"1801",	"1802",	"1802",	"1803",	"1804",	"1804",	"1805",	"1807",	"1808",	"1809",	"1810",	"1811",	"1812",	"1813",	"1814",	"1815",	"1816",	"1890",	"1891",	"1896",	"1897",	"1898",	"1901",	"1902",	"1903",	"1904",	"1905",	"1905",	"1905",	"1906",	"1907",	"1908",	"1909",	"1910",	"1911",	"1912",	"1913",	"1914",	"1915",	"1916",	"1917",	"1918",	"1919",	"1919",	"1921",	"1922",	"1922",	"1982",	"1984",	"1988",	"1988",	"1988",	"1992",	"1994",	"1995",	"1997",	"2001",	"2002",	"2002",	"2003",	"2004",	"2005",	"2005",	"2006",	"2007",	"2008",	"2097",	"2099",	"2101",	"2102",	"2103",	"2104",	"2105",	"2106",	"2107",	"2108",	"2196",	"2197",	"2198",	"2199",	"2201",	"2201",	"2296",	"2297",	"2298",	"2299",	"1981",	"Bolívar",	"Brisas Del Río",	"Dagua",	"El Hormiguero",	"El Hormiguero",	"El Hormiguero",	"El Hormiguero",	"El Hormiguero",	"El Hormiguero",	"El Hormiguero",	"El Hormiguero",	"El Hormiguero",	"El Hormiguero",	"El Saladito",	"El Saladito",	"El Saladito",	"Felidia",	"Felidia",	"Felidia",	"Felidia",	"Fray Pena",	"Jamundi",	"Juan Pablo II",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Buitrera",	"La Castilla",	"La Castilla",	"La Castilla",	"La Castilla",	"La Cumbre",	"La Elvira",	"La Elvira",	"La Leonera",	"La Nueva Estancia",	"Los Andes - Corregimiento",	"Los Andes - Corregimiento",	"Los Andes - Corregimiento",	"Los Andes  Corregimiento",	"Los Andes  Corregimiento",	"Los Andes  Corregimiento",	"Los Andes  Corregimiento",	"Los Andes  Corregimiento",	"0597",	"0594",	"1785",	"1781",	"1781",	"Navarro",	"Navarro",	"Navarro",	"0315",	"Nuevo Horizonte",	"Pance",	"Pance",	"Pance",	"Pance",	"Pance",	"Pance",	"Pance",	"Pance",	"Pance",	"Pance",	"Pance",	"Pance",	"Pance",	"Panorama",	"Pichinde",	"Pichinde",	"2195",	"0410",	"Puerto Isaac",	"San Jorge",	"0805",	"1399",	"0408",	"1983",	"Trinidad I",	"Trinidad I",	"1999",	"2098",	"2098",	"Vijes",	"0599",	"Villacarmelo",	"Villacarmelo",	"Villacarmelo",	"2194",	"Yumbo",	"Yumbo",	"Acopi",	"Felidia",	"Golondrinas",	"Hormiguero",	"La Buitrera",	"La Castilla",	"La Elvira",	"La Leonera",	"Monte Bello",	"Montebello",	"Montebello",	"Navarro",	"Pance",	"Pichinde",	"Saladito",],
        }

In [25]:
# Se crea el dataframe con el diccionario de datos referente a los nombre de los barrios para el posterior cruce de información
df_barrios = pd.DataFrame(dict_barrios, columns = ['BARRIO_REG', 'NOM_BAR', 'COD_BAR'])

In [26]:
# Para el cruce de las bases de datos se hace la identificación de valores unicos en la columna de barrios de la base de datos de Registro Mercantil limpia
#pd.set_option('display.max_rows', None)
#df3.groupby('BARRIO')['MATRICULA'].nunique()

In [27]:
# Para unir las bases es necesario volver las llaves en mayuscula en mabos dataframes
df3['BARRIO2'] = df3['BARRIO'].str.upper()
df_barrios['BARRIO_REG2'] = df_barrios['BARRIO_REG'].str.upper()

In [28]:
df_barrios.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 472 entries, 0 to 471
Data columns (total 4 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   BARRIO_REG   472 non-null    object
 1   NOM_BAR      472 non-null    object
 2   COD_BAR      472 non-null    object
 3   BARRIO_REG2  472 non-null    object
dtypes: object(4)
memory usage: 14.9+ KB


In [29]:
# Se unen las dos bases de datos para obtener la información de los barrios corregidos
#df4 = pd.merge(df3,df_barrios, on=['BARRIO2', 'BARRIO_REG2'])

#Falta hacer bien el merge

In [30]:
#pd.set_option('display.max_rows', None)
#df3.groupby('BARRIO2')['MATRICULA'].nunique()

In [31]:
#pd.set_option('display.max_rows', None)
#df_barrios.groupby('BARRIO_REG2')['COD_BAR'].nunique()

<p>----</p>

In [34]:
# Para guardar la base de datos lista para ser tratada en formato Excel
df3.to_excel(r'RM_2019_V5.xlsx', index = False)